In [86]:
!pip install -r requirements.txt
!pip install tabulate
!pip install scipy
import numpy as np
import sys
from tabulate import tabulate
import scipy.special

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


In [87]:
from PIL import Image

def save_images_as_png(images_array, prefix="image"):
    for i, image_array in enumerate(images_array):
        # Convert the image array to PIL Image
        image = Image.fromarray(image_array)
        # Save the image as PNG with a sequential filename
        filename = f"{prefix}_{i}.png"
        image.save(f"images/{filename}")

def read_images_from_binary_file(path):
    with open(path,"rb") as file:
        magic_number=file.read(4)
        number_of_items = int.from_bytes(file.read(4), byteorder='big')
        number_of_rows = int.from_bytes(file.read(4), byteorder='big')
        number_of_columns = int.from_bytes(file.read(4), byteorder='big')
        image_data=file.read()
        size=number_of_rows*number_of_columns

    images_array=np.frombuffer(image_data,dtype=np.uint8)
    images_array = images_array.reshape((number_of_items, number_of_columns, number_of_rows))
    return images_array

def read_training_set_label_file(filename):
    with open(filename, 'rb') as file:
        # Read the magic number and other metadata
        magic_number = int.from_bytes(file.read(4), byteorder='big')
        num_labels = int.from_bytes(file.read(4), byteorder='big')

        # Read the label data
        label_data = np.frombuffer(file.read(num_labels), dtype=np.uint8)

    return label_data

training_data=read_images_from_binary_file("data/train-images.idx3-ubyte")
training_label=read_training_set_label_file("data/train-labels.idx1-ubyte")
testing_data=read_images_from_binary_file("data/t10k-images.idx3-ubyte")
testing_label=read_training_set_label_file("data/train-labels.idx1-ubyte")



In [88]:
learning_rate=0.01
def sigmoid(x):
    return scipy.special.expit(x)

def sigmoid_derivative(x):
    sigmoid_x = sigmoid(x)
    return sigmoid_x * (1 - sigmoid_x)


class Layer:
   def __init__(self, Values):
      self.values = Values /255
      self.delta_values=np.zeros(self.values.size)

      self.zvalues= np.zeros(self.values.size)
      self.delta_zvalues=np.zeros(self.values.size)

      self.weights = None
      self.delta_weights= None
      
      self.biases = None
      self.delta_biases = None
      
      self.next_layer=None
      self.previous_layer=None
      self.layer_number=1
      
      

   def nextLayer(self,nodes):
      self.weights = np.random.uniform(low=-1, high=1, size=(self.values.size, nodes)) *0.1
      self.delta_weights =  np.zeros((self.values.size,nodes))

      biases = np.random.uniform(low=-1, high=1, size=nodes) *0.1

      values= np.dot(self.values.reshape(1, self.values.size),self.weights).flatten() + biases

      zvalues=values
      for i,value in enumerate(values):
         value=sigmoid(value)
         values[i]=value   
         
      layer=Layer(values)
      layer.layer_number=self.layer_number+1
      layer.delta_biases = np.zeros(nodes)    
      layer.biases = biases
      self.next_layer=layer
      layer.zvalues=zvalues
      layer.previous_layer=self
      return layer
    
    
    
   def forward(self, image):
      image=image.flatten() /255
      layer = self
      layer.values = image
      while layer.next_layer is not None:
         z_values = np.dot(layer.values.T, layer.weights).T + layer.next_layer.biases
         layer.next_layer.zvalues = np.copy(z_values)
         layer.next_layer.values = np.copy(sigmoid(z_values))
         layer = layer.next_layer
      
      return layer.values
      

    
   def backward(self,expectation):
      layer=self
      while layer.next_layer!=None:
         layer=layer.next_layer
         
      for i,value in enumerate(layer.values):
         layer.delta_values[i]=2*(value-expectation[i])
         layer.delta_zvalues[i]=layer.delta_values[i] * sigmoid_derivative(layer.zvalues[i])
      
      layer.delta_biases=np.copy(layer.delta_zvalues)
      layer=layer.previous_layer
      while layer.previous_layer!=None:
         for i, row in enumerate(layer.weights):
            for j, value in enumerate(row):
               layer.delta_weights[i][j]=layer.previous_layer.delta_zvalues[j] * layer.values[i]


         for i, val in enumerate(layer.values):
            new=0
            next_layer=layer.next_layer
            for j, value in enumerate(next_layer.delta_zvalues):
               new+=value * layer.weights[i][j]
            layer.delta_values[i]=new


         for i,value in enumerate(layer.zvalues):
            layer.delta_zvalues[i]=layer.delta_values[i] * sigmoid_derivative(layer.zvalues[i])

         layer.delta_biases=np.copy(layer.delta_zvalues)
         layer=layer.previous_layer

         # if layer.layer_number==2:
         #    print(layer.values)
         
      

      layer = self

      while layer.next_layer!=None:
         if layer.biases is not None:
            layer.biases=layer.biases-learning_rate * layer.delta_biases
         layer.weights=layer.weights-learning_rate * layer.delta_weights
         layer=layer.next_layer
         
      print(costFunction(layer.values,expectation))
      
      
      
   def outcome(self):
      layer=self
      while layer.next_layer!=None:
         layer=layer.next_layer
      return layer.values
    
   def test_layer(self):
      layer = self
      while layer is not None:
         print("Layer Values Shape:", layer.values.shape)
         print("Layer Weights Shape:", layer.weights.shape if layer.weights is not None else None)
         print("Layer Biases Shape:", layer.biases.shape if layer.biases is not None else None)
         print("Layer Z Values Shape:", layer.zvalues.shape)
         print("Layer Delta Values Shape:", layer.delta_values.shape)
         print("Layer Delta Weights Shape:", layer.delta_weights.shape if layer.delta_weights is not None else None)
         print("Layer Delta Biases Shape:", layer.delta_biases.shape if layer.delta_biases is not None else None)
         print("-------------------------------------------")
         layer = layer.next_layer

   def print_weights_and_biases(self):
    layer = self
    while layer is not None:
        print(f"Layer {layer.layer_number}:")
        if layer.weights is not None:
            print("Weights:")
            print(layer.weights)
        if layer.biases is not None:
            print("Biases:")
            print(layer.biases)
        print("-------------------------------------------")
        layer = layer.next_layer

   
   def print_values(self):
      layer = self
      while layer is not None:
         print(f"Layer {layer.layer_number}:")
         if layer.values is not None:
               print("Vals:")
               print(layer.values)
         print("-------------------------------------------")
         layer = layer.next_layer
   
    

In [89]:


def costFunction(actual, expectation):
    cost = 0
    for i, value in enumerate(actual):
        cost += (value - expectation[i])**2
    return cost


def digit(number):
    arr=np.zeros(10)
    arr[number]=1
    return arr

def number_from_digit(arr):
    return np.argmax(arr)

sample_image=training_data[10]
first_layer=Layer(sample_image)
fourth_layer=first_layer.nextLayer(10)
# print(first_layer.weights)
# print(second_layer.biases)
# print("first layer",first_layer.values)
# print("Second layer",second_layer.values)
# print("trd layer",third_layer.values)

for i,Image in enumerate(training_data):
    if(i>60000):
        break
    first_layer.forward(Image)
    first_layer.backward(digit(training_label[i]))
    print(fourth_layer.values)



2.3915340701380474
[0.69105093 0.48273557 0.56189373 0.48921547 0.47595366 0.80781823
 0.59451617 0.47162875 0.33640099 0.4163871 ]
2.5693083430927097
[0.61768606 0.44518061 0.64698296 0.60201948 0.38638182 0.72385152
 0.39781222 0.65309259 0.19019764 0.38695301]
2.1035136516086665
[0.52035391 0.37626138 0.44667409 0.49803126 0.53732395 0.60978214
 0.38025591 0.45749652 0.31537511 0.45205916]
2.619425201494349
[0.3640996  0.74092255 0.52570516 0.52862061 0.45016247 0.68737301
 0.57953894 0.57441665 0.55792394 0.46011195]
2.965607169877333
[0.5866775  0.48142764 0.5982956  0.68607963 0.38474187 0.56697142
 0.29418332 0.63890415 0.3132964  0.29388291]
2.701501876307537
[0.49767234 0.62733531 0.40118426 0.54930218 0.53335122 0.55611124
 0.29443367 0.52170329 0.3351703  0.57882078]
3.026253466755919
[0.75461487 0.43128401 0.41914454 0.56423392 0.41060266 0.67014679
 0.45402192 0.54609967 0.41237248 0.58925958]
2.5940421175520894
[0.39960873 0.63351824 0.48483965 0.53385138 0.53668217 0.656

In [90]:

print(first_layer.forward(training_data[73]),training_label[72])
# print(third_layer.values)
print(first_layer.forward(training_data[250]),training_label[250])
# print(third_layer.values)







[0.44823345 0.47276064 0.41980475 0.51112703 0.32444627 0.66067357
 0.31498374 0.52406375 0.40224481 0.6493836 ] 1
[0.48918944 0.55078854 0.38171863 0.44970019 0.42468607 0.82105038
 0.21430933 0.53902993 0.52466012 0.57076715] 3


In [91]:
# first_layer.test_layer()
# first_layer.print_weights_and_biases()
# first_layer.print_values()